# System Neuroscience - Sound localization

This is a Jupyter Notebook. The code you see is written in [Python 3](https://www.python.org/).

Audio samples in this Notebook are to be played via headphones or earphones to enable perception of sound localization cues.

<div style="border: 5px solid red; color: black; padding: 0.5em; margin: 1em;"><strong>WARNING:</strong><br>The Audio-Elements in Jupyter Notebooks may play very loud sounds.<br>You should <strong>turn down the volume</strong> in your operating system (Windows/macOS) or the media volume when using a phone.<br>Increase volume stepwise, starting with a low level until you can hear the audio samples just fine.<br><strong>Be careful to avoid noise damage or discomfort!</strong></div>

## Just view it and play Audio samples:

When you open the Notebook in a suitable environment that renders it correctly, the output `<Audio>` elements should be shown in your browser right away as they are saved together with the Notebook.

If you have no Python/Jupyter installed on your computer, just visit:

https://colab.research.google.com/github/penalab/systems-sound-localization/blob/master/Sys_Audio_Class.ipynb

## Play with parameters:

If you want to play around with the code and change parameters, there are two alternatives:

### Google's Colaboratory

**Requires:** Google account

1. Login to your Google Account
2. Visit the linke to the Notebook in Google's "Colaboratory":  
   https://colab.research.google.com/github/penalab/systems-sound-localization/blob/master/Sys_Audio_Class.ipynb
3. On the top-right, click "Connect" (or the little arrow right of it and then "Connect to hosted runtime".
4. Now you can "run" (mean: execute) the Python code of the individual code cells by clicking on the "Play" icon in the top-left corner of any cells containing Python code. After running the first code cell (the one with `import numpy as np` near the beginning) once, you are free to play around.
5. You can save your changes into your personal Google Drive.

### Execute Jupyter locally

**Requires:** Python 3 installed on your computer, plus at least `numpy`, `jupyter` and all of their dependencies. All of this comes bundles in the [Anaconda Distribution](https://www.anaconda.com/download/). Make sure you have Python 3.6 or 3.7.

You can then download the Notebook file [Sys_Audio_Class.ipynb](https://github.com/penalab/systems-sound-localization/raw/master/Sys_Audio_Class.ipynb) from Github, place it in some directory where you find it in Jupyter and run it as usual.

## Notes

In between the Python Code cells (each having an input area with code and, possibly, an output area), there may be text areas (like this one). These are Markdown cells. If you accidentally start editing one of these, is looks less like nicely formatted text but more like a colored text editor. You can "execute" those cells in order to recover the formatted version.

In [1]:
#####################################################
## This code cell must be executed once before the ##
## others. It defines all the necessary functions. ##
#####################################################

%matplotlib notebook
import matplotlib.pyplot as plt
import numpy as np
from IPython.display import Audio, HTML
import struct
from io import BytesIO
import wave

# Default sampling rate:
samplingrate = 48000

def db2amp(d):
    return 10 ** (float(d) / 20)
def amp2db(f):
    return 20 * np.log10(f)

def us2s(microseconds):
    return microseconds * 1e-6
def s2us(seconds):
    return seconds * 1e6

def ms2s(m_seconds):
    return m_seconds * 1e-3
def s2ms(seconds):
    return seconds * 1e3

def times(signal):
    if isinstance(signal, (tuple, list)):
        signal = signal[0]
    return np.arange(signal.size)/samplingrate

def signal_energy(signal, fs=100e3):
    #signal = signal.astype(np.float64)
    #print np.min(signal), np.max(signal)
    return np.sum(signal.astype(np.float64) ** 2) / fs

def signal_power(signal, fs=100e3):
    return signal_energy(signal, fs=fs) / signal.size

def band_limits(center=8500, octave_width=1.0):
    return float(center) * 2**(-.5*octave_width), float(center) * 2**(+.5*octave_width)

def to_stereo(signal):
    """Return a tuple of left and right signal
    A single signal will be duplicated.
    A stereo signal will be returned unchanged.
    """
    try:
        signal_L, signal_R = signal
        #print "Play: Stereo"
    except ValueError:
        signal_L = signal
        signal_R = signal
        #print "Play: Mono"
    return (signal_L, signal_R)

def ramp(x = None, start = 0.0, stop = 1.0, ramp_dur = .005, fs = None, amp = 1.0):
    """ramp(x = np.ones(fs), start = .400, stop = .500, ramp_dur = .005, fs = fs, amp = 1.0)
    
    Ramp the signal x by linaer ramps between start and stop
    
    Examples
    ========
    
    >>> ramp()
    returns the default ramp function as it generates internally data x as all ones for 1 s with fs.
    """
    if fs is None:
        fs = samplingrate
    if x is None:
        x = np.ones(int(fs))
    t1 = start
    t2 = (start + ramp_dur)
    t3 = (stop - ramp_dur)
    t4 = stop
    t = np.arange(x.size) / fs
    r = amp * np.piecewise(t, [(t1 <= t) & (t < t2), (t2 <= t) & (t < t3), (t3 <= t) & (t < t4)],
                         [lambda t: (t - t1) / (t2-t1), 1, lambda t: 1 - (t - t3) / (t4-t3), 0])
    return r * x

def bandpass_itd_noise(min_freq = 20, max_freq = 20000, itd=0, fs=None, samples = None):
    """bandpass_itd_noise()
    """
    # Calculate available fft frequencies:
    if fs is None:
        fs = samplingrate
    if samples is None:
        samples = int(fs)
    freqs = np.fft.rfftfreq(samples, 1/fs)
    f = np.zeros_like(freqs)
    idx = np.where(np.logical_and(freqs>=min_freq, freqs<=max_freq))[0]
    f[idx] = 1 * np.sqrt(.5 * samples) * (f.size / np.count_nonzero(idx))**.5
    f = np.array(f, dtype='complex')

    phases_rad = np.random.rand(len(f)) * 2 * np.pi
    phases = np.cos(phases_rad) + 1j * np.sin(phases_rad)

    itd_phas_rad = us2s(itd) * np.pi * freqs #  * .5 * 2
    shift_left = np.cos(-itd_phas_rad) + 1j * np.sin(-itd_phas_rad)
    shift_right = np.cos(+itd_phas_rad) + 1j * np.sin(+itd_phas_rad)
    phases_left = phases * shift_left
    phases_right = phases * shift_right

    f_left = f * phases_left
    f_right = f * phases_right

    s_left = np.fft.irfft(f_left).real
    s_right = np.fft.irfft(f_right).real
    return s_left, s_right

def do_ild(signal, ild = 0):
    signal_L, signal_R = to_stereo(signal)
    amp_L = db2amp(-.5 * ild)
    amp_R = db2amp(+.5 * ild)
    return amp_L * signal_L, amp_R * signal_R

def do_bc(signal, bc = 100, **noise_kwargs):
    signal_L, signal_R = to_stereo(signal)
    if bc != 100:
        if bc < 0:
            signal_R = -signal_R
        r = abs(bc / 100)
        _, decorr_noise_L = bandpass_itd_noise(itd=0, **noise_kwargs)
        _, decorr_noise_R = bandpass_itd_noise(itd=0, **noise_kwargs)
        # Adjust powers:
        decorr_noise_L = decorr_noise_L / (signal_power(decorr_noise_L) / signal_power(signal_L))**.5
        decorr_noise_R = decorr_noise_R / (signal_power(decorr_noise_R) / signal_power(signal_R))**.5
        signal_L = r**.5 * signal_L + (1 - r)**.5 * decorr_noise_L
        signal_R = r**.5 * signal_R + (1 - r)**.5 * decorr_noise_R
    return signal_L, signal_R

def stack(*signals):
    n = len(signals)
    signal_stack = tuple(np.sum(np.stack([s[c] for s in signals]), axis=0) / np.sqrt(n) for c in (0, 1))
    return signal_stack

def pscale(signal, rel_power=1.0):
    scaled_signal = tuple(signal[c] * np.sqrt(rel_power) for c in (0, 1))
    return scaled_signal

def player(signal, rel_abi=0):
    # Make it stereo and stack in one 
    signal = np.vstack(to_stereo(signal))
    scaled = signal.T.ravel() * 1024 * db2amp(rel_abi)
    if np.max(np.abs(scaled)) > 32767:
        scale_by = 32767 / np.max(np.abs(scaled))
        scaled = scaled * scale_by
        import sys
        print(f"Signal would have clipped. Scaled (down) by {amp2db(scale_by):.1g} dB.", file=sys.stderr)
    fp = BytesIO()
    waveobj = wave.open(fp,mode='wb')
    waveobj.setnchannels(2)
    waveobj.setframerate(samplingrate)
    waveobj.setsampwidth(2)
    waveobj.setcomptype('NONE','NONE')
    waveobj.writeframes(b''.join([struct.pack('<h',x) for x in np.int16(scaled)]))
    pmc_data = fp.getvalue()
    waveobj.close()
    display(Audio(pmc_data, rate=samplingrate, autoplay=False))

def save_wave(signal, filename, rel_abi=0):
    # Make it stereo and stack in one 
    signal = np.vstack(to_stereo(signal))
    scaled = signal.T.ravel() * 1024 * db2amp(rel_abi)
    if np.max(np.abs(scaled)) > 32767:
        scale_by = 32767 / np.max(np.abs(scaled))
        scaled = scaled * scale_by
        import sys
        print(f"Signal would have clipped. Scaled (down) by {amp2db(scale_by):.1g} dB.", file=sys.stderr)
    with open(filename, 'wb') as fp:
        waveobj = wave.open(fp,mode='wb')
        waveobj.setnchannels(2)
        waveobj.setframerate(samplingrate)
        waveobj.setsampwidth(2)
        waveobj.setcomptype('NONE','NONE')
        waveobj.writeframes(b''.join([struct.pack('<h',x) for x in np.int16(scaled)]))
        waveobj.close()

def noise(min_freq = 20, max_freq = 20000, itd=0, ild=0, bc=100, length=1.0, level=0, ramp_dur=0.005, show_player=True, return_signal=False):
    samples = int((length + 0.010) * samplingrate)
    signal_LR = bandpass_itd_noise(min_freq, max_freq, itd, samplingrate, samples)
    signal_LR = do_bc(signal_LR, bc=bc, min_freq=min_freq, max_freq=max_freq, fs=samplingrate, samples=samples)
    signal_LR = do_ild(signal_LR, ild)
    signal_LR = [ramp(s, start=0.005, stop=length+0.005, ramp_dur=ramp_dur) for s in signal_LR]
    if show_player:
        display(HTML(f'<p><strong>Noise</strong> {min_freq}-{max_freq} Hz, '
                     f'ITD = {itd} μs, ILD = {ild} dB, BC = {bc}%'
                     '</p><style type="text/css">audio {min-width: 400px; }</style>'))
        player(signal_LR, rel_abi=level)
    if return_signal:
        return signal_LR

def tone(freq = 440, itd=0, ild=0, bc=100, length=1.0, level=0, ramp_dur=0.005, show_player=True, return_signal=False, **bc_noise_kwargs):
    samples = int((length + 0.010) * samplingrate)
    t = np.arange(0, samples) / samplingrate
    phase = np.random.rand(1) * 2 * np.pi
    shift = us2s(itd) * np.pi * freq
    signal_LR = (
        np.sin(t * 2 * np.pi * freq + phase - shift),
        np.sin(t * 2 * np.pi * freq + phase + shift)
    )
    signal_LR = do_bc(signal_LR, bc=bc, fs=samplingrate, samples=samples, **bc_noise_kwargs)
    signal_LR = do_ild(signal_LR, ild)
    signal_LR = [ramp(s, start=0.005, stop=length+0.005, ramp_dur=ramp_dur) for s in signal_LR]
    if show_player:
        display(HTML(f'<p><strong>Tone</strong> {freq} Hz, '
                     f'ITD = {itd} μs, ILD = {ild} dB, BC = {bc}%'
                     '</p><style type="text/css">audio {min-width: 400px; }</style>'))
        player(signal_LR, rel_abi=level)
    if return_signal:
        return signal_LR

def tone_stack(freqs = np.arange(500, 12000, 1000), show_player=True, return_signal=False, show_single_player=False, **tone_kwargs):
    tone_kwargs.update(show_player=show_single_player)
    tone_kwargs.update(return_signal=True)
    signal_LR = stack(*[tone(freq=f, **tone_kwargs) for f in freqs])
    if show_player:
        display(HTML(f'<p><strong>Tone-Stack</strong> {freqs} Hz, '
                     f'ITD = {tone_kwargs.get("itd",0)} μs, ILD = {tone_kwargs.get("ild",0)} dB, BC = {tone_kwargs.get("bc",100)}%'
                     '</p><style type="text/css">audio {min-width: 400px; }</style>'))
        player(signal_LR)
    if return_signal:
        return signal_LR



## Localize Broadband Noise

The following two cells include each several 1-second broadband noise samples.

### ITD

In the first cell, the __interaural time differnce (ITD)__ was varied from `-600` µs to `+600` µs.

By convention, _negative ITDs_ indicate that the sound presented to the _left_ ear is leading, _positive ITDs_ indicate that the sound presented to the _right_ ear is leading.

This kind of sound that include "only" ITD information is usually perceived "inside the head", i.e. it is internalized. However, sound with different ITDs should be clearly shifted inside the head according to the ITD value.

In [ ]:
for itd in [-4800, -2400, -1200, -900, -750, -600, -450, -300, -150, 0, 150, 300, 450, 600, 750, 900, 1200, 2400, 4800]:
    noise(itd=itd, length=.5)

### ILD

In the second cell, the __interaural level differnce (ILD)__ was varied from `-20` dB to `+20` dB.

By convention, _negative ILDs_ indicate that the sound presented to the _left_ ear is louder, _positive ILDs_ indicate that the sound presented to the _right_ ear is louder.

**Note:** Due to the way the `<Audio>` element is generated by Jupyter and presented by the Browser, including a normalization step, stimuli with larger absolute ILD values may appear softer. This is a side effect of the normalization and _not_ of ILD alone.

Like ITD-only sounds, ILD-only sounds are internalized.

In [3]:
for ild in [-30, -20, -15, -10, -5, 0, 5, 10, 15, 20, 30]:
    noise(ild=ild, length=.5)

# ITD detection varying frequency and bandwidth

In [12]:
bw = 400
cf = 700
for itd in [-600, -450, -300, -150, 0, 150, 300, 450, 600]:
    noise(min_freq=cf-bw/2, max_freq=cf+bw/2, itd=itd, length=.5)


In [13]:
bw = 400
cf = 7000
for itd in [-600, -450, -300, -150, 0, 150, 300, 450, 600]:
    noise(min_freq=cf-bw/2, max_freq=cf+bw/2, itd=itd, length=.5)


## Binaural Correlation

In [14]:
for bc in [100, 80, 60, 40, 20, 0]:
    print(f"Binaural Correlation {bc}%")
    noise(itd=-300, bc=bc)
    noise(itd=   0, bc=bc)
    noise(itd= 300, bc=bc)


Binaural Correlation 100%


Binaural Correlation 80%


Binaural Correlation 60%


Binaural Correlation 40%


Binaural Correlation 20%


Binaural Correlation 0%
